In [1]:
# PEA implementation of stochastic growth model adapted from Fabrice Collard's Matlab code, http://fabcol.free.fr/
# tested in Julia 0.6.1.1
# this code is part of chapter 5, "Advanced Numerical Techniques" from the book: "Introduction to Quantitative Macroeconomics with Julia"
# Academic Press - Elsevier
# for comments, email at: petre(dot)caraiani(at)gmail(dot)com

# set algorithm parameters
long  = 200;
init  = 50;
slong = init+long;
T     = init+1:slong-1;
T1    = init+2:slong;
tol   = 1e-6;
crit  = 1;

#set model parameters
gam     = 1;
sigma   = 1;
delta   = 0.1;
beta    = 0.95;
alpha   = 0.3;
ab      = 0;
rho     = 0.9;
se      = 0.01;

#steady state
ksy =(alpha*beta)/(1-beta*(1-delta));
yss = ksy^(alpha/(1-alpha));
kss = yss^(1/alpha);
iss = delta*kss;
css = yss-iss;
csy = css/yss;
lss = css^(-sigma);

In [2]:
#generate own shocks
#using(DataFrames)
srand(1)
e   = se*randn(slong,1);
#ee = DataFrame(e)
#writetable("output.csv", ee);
#load shocks from Collard(2015) generated in Matlab to find the same solution
e=readdlm("e1_noise.csv");

In [3]:
a   = zeros(slong,1);
a[1]=  ab+e[1];
for i=2:slong;
a[i]=rho*a[i-1]+(1-rho)*ab+e[i];
end

In [4]:
#initial solution
ncont  = 3;                  # of static equations
nbend  = 1;                  # endogenous predetermined variables
nshoc  = 1;                  # of shocks
nback  = nbend+nshoc;        # of state variables
nforw  = 1;                  # of costate variables
nstat  = nback+nforw;        # of state and costate variables
Mcc    = zeros(ncont,ncont);
Mcs    = zeros(ncont,nstat);
Mss0   = zeros(nstat,nstat);
Mss1   = zeros(nstat,nstat);
Msc0   = zeros(nstat,ncont);
Msc1   = zeros(nstat,ncont);
Mse    = zeros(nstat,nshoc);

In [5]:
#setup the matrices
# Output
Mcc[1,1] = 1;
Mcs[1,1] = alpha;
Mcs[1,2] = 1;

# investment
Mcc[2,1] = 1;
Mcc[2,2] = -iss/yss;
Mcc[2,3] = -css/yss;

# consumption
Mcc[3,3] = -sigma;
Mcs[3,3] = 1;

# capital
Mss0[1,1] = 1;
Mss1[1,1] = delta-1;
Msc1[1,2] = delta;

# technology shock
Mss0[2,2] = 1;
Mss1[2,2] = -rho;
Mse[2,1]  = 1;

# Euler
Mss0[3,1] = (1-beta*(1-delta));
Mss0[3,3] = -1;
Mss1[3,3] = 1;
Msc0[3,1] = (1-beta*(1-delta));

In [6]:
# Solving the system   
M0=inv(Mss0-Msc0*inv(Mcc)*Mcs);
M1=(Mss1-Msc1*inv(Mcc)*Mcs);
W=-M0*M1;

# MU -> eigenvalues, P -> eigenvectors
v,w = eig(W)
r=[abs.(v) w']
vsize=size(v,1)
for i = 1:vsize
    for j = i+1:vsize
        if  real(r[i,1])> real(r[j,1])
            tmp = r[i,:];
            r[i,:]=r[j,:];
            r[j,:]=tmp;
        elseif real(r[i,1])== real(r[j,1])
            if imag(r[i,1])> imag(r[j,1])
            tmp = r[i,:];
            r[i,:]=r[j,:];
            r[j,:]=tmp;   
            end;    
        end;
    end;     
end;

lam= r[:,1];
P=r[:,2:4]';

Q=inv(P);
lam=diagm(lam);

In [7]:
#Direct solution
Gamma=-inv(Q[nback+1:nstat,nback+1:nstat])*Q[nback+1:nstat,1:nback];
MSS=W[1:nback,1:nback]+W[1:nback,nback+1:nstat]*Gamma;
PI=inv(Mcc)*(Mcs[:,1:nback]+Mcs[:,nback+1:nstat]*Gamma);
MSE=[zeros(nbend,nshoc);eye(nshoc)];


In [8]:
S  = zeros(nback,long+init);
S[:,1]= MSE*e[1];
for i = 2:long+init;
   S[:,i]= MSS*S[:,i-1]+MSE*e[i];
end;

In [9]:
lb = Gamma*S;
lb = lss*exp.(lb);
lbv= vec(lb);
k  = log(kss)+S[1,:];
kv = vec(k);
ek = exp.(kv);
a  = S[2,:];
av = vec(a);
ea = exp.(av);
T  = init+1:init+long-1;
T1 = init+2:init+long;

In [10]:
XX  = [ones(long-1,1) kv[T] av[T] kv[T].*kv[T] av[T].*av[T] kv[T].*av[T]];
yy  = log.(beta*lb[T1].*(alpha*ea[T1].*ek[T1].^(alpha-1)+1-delta));
b0 = \(XX,yy);

In [11]:
#Main Loop
iter=1;
crit=1;
while crit>tol
k  = zeros(slong+1,1);
lb = zeros(slong,1);
X  = zeros(slong,length(b0));
k[1]= kss;
for i= 1:slong;
  X[i,:]= [1 log.(k[i]) a[i] log(k[i])*log(k[i]) a[i]*a[i] log(k[i])*a[i]];
  lb[i]  = exp.(X[i,:]'*b0);
  k[i+1] = exp.(a[i])*k[i]^alpha+(1-delta)*k[i]-lb[i]^(-1/sigma);
end
y    = beta*lb[T1].*(alpha*exp.(a[T1]).*k[T1].^(alpha-1)+1-delta);
bt   = X[T,:]\log.(y);
b    = copy(gam*bt+(1-gam)*b0);
crit = maximum(abs.(b-b0));
b0   = copy(b);
println("solution",b0)
iter=iter+1;
end;


solution[1.63964, -3.00701, 1.60307, 1.27846, 1.46655, -2.19256]
solution[1.76819, -3.27105, 1.53844, 1.41379, 1.47546, -2.12414]
solution[1.83915, -3.41625, 1.44735, 1.48787, 1.49376, -2.0291]
solution[1.88338, -3.50636, 1.37241, 1.53361, 1.51939, -1.9512]
solution[1.91351, -3.5675, 1.31829, 1.56453, 1.54463, -1.89512]
solution[1.93547, -3.61199, 1.28147, 1.58698, 1.56597, -1.85714]
solution[1.95228, -3.646, 1.2573, 1.60412, 1.58271, -1.83232]
solution[1.96553, -3.67281, 1.24174, 1.61765, 1.59534, -1.81647]
solution[1.97611, -3.69424, 1.2318, 1.62847, 1.60468, -1.80643]
solution[1.98458, -3.71142, 1.2254, 1.63715, 1.61152, -1.80003]
solution[1.99135, -3.72515, 1.22119, 1.6441, 1.61652, -1.79587]
solution[1.99673, -3.73607, 1.21832, 1.64963, 1.62019, -1.79307]
solution[2.00098, -3.74469, 1.2163, 1.654, 1.62291, -1.79111]
solution[2.00431, -3.75145, 1.21483, 1.65743, 1.62494, -1.78968]
solution[2.00691, -3.75674, 1.21371, 1.66011, 1.62646, -1.78861]
solution[2.00894, -3.76086, 1.21286, 

In [12]:
#Pkg.add("Plots")
#Pkg.add("PlotlyJS")
#using PlotlyJS
using Plots
plotly() # Choose the Plotly.jl backend for web interactivity
#plot(k',c',linewidth=1,label="Consumption",title="Consumption vs capital stock")
scatter(k[T],k[T1],label="Capital Stock",title="k(t+1) vs. k(t)")

#Plots.plotlyjs()   # specify backend

#scatter!(k[T],k[T1], color=:blue,  label="k")